In [1]:
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm

import plotly.graph_objs as go
import plotly.io as pio
pio.templates.default = 'plotly_white'

In [2]:
def mc_step(N, R):
    U = np.random.uniform(0, R**3, size=N)**(1/3)
    x = np.random.randn(N)
    y = np.random.randn(N)
    z = np.random.randn(N)
    mag = np.sqrt(x**2 + y**2 + z**2)
    x = U * x / mag
    y = U * y / mag
    z = U * z / mag
    return x, y, z

In [3]:
x, y, z = mc_step(20000, 17.7)

fig = go.Figure()

fig.add_trace(
    go.Scatter3d(
        x=x,
        y=y,
        z=z,
        mode='markers',
        marker=dict(size=0.9)
    )
)

fig.show()

In [4]:
f = []
R_cuts = np.linspace(14, 17.2, 33)
steps = 1000
number_of_points = 100000
R_lim = 17.7
r_res = 0.1
for _ in tqdm(range(steps), leave=False):
    x, y, z = mc_step(number_of_points, R_lim)
    x += r_res * np.random.randn(number_of_points)
    y += r_res * np.random.randn(number_of_points)
    z += r_res * np.random.randn(number_of_points)
    R = np.sqrt(x**2 + y**2 + z**2)
    f.append([R[R<R_cut].shape[0] / number_of_points for R_cut in R_cuts])
    
f = np.array(f)
f_mean = f.mean(axis=0)
f_std = f.std(axis=0)

f_df = pd.DataFrame(np.transpose([f_mean, f_std]), columns=['f', 'df'])
f_df

  0%|          | 0/1000 [00:00<?, ?it/s]

f        df
0   0.494735  0.001579
1   0.505424  0.001593
2   0.516265  0.001594
3   0.527259  0.001567
4   0.538401  0.001553
5   0.549719  0.001532
6   0.561170  0.001537
7   0.572781  0.001528
8   0.584544  0.001526
9   0.596477  0.001506
10  0.608577  0.001508
11  0.620826  0.001495
12  0.633257  0.001480
13  0.645835  0.001465
14  0.658592  0.001476
15  0.671494  0.001472
16  0.684578  0.001457
17  0.697834  0.001457
18  0.711267  0.001424
19  0.724854  0.001381
20  0.738604  0.001361
21  0.752528  0.001330
22  0.766626  0.001319
23  0.780907  0.001310
24  0.795388  0.001284
25  0.810004  0.001242
26  0.824827  0.001209
27  0.839827  0.001186
28  0.855011  0.001156
29  0.870366  0.001094
30  0.885923  0.001046
31  0.901670  0.000977
32  0.917598  0.000872

In [5]:
f_df.to_csv('plots/f_df.csv', index=False)

In [6]:
fig = go.Figure()
for i in range(f.shape[1]):
    fig.add_trace(
        go.Histogram(
            x=f[:, i],
            showlegend=False,
            visible=(i==0)
        )
    )

buttons = []
for j in range(f.shape[1]): 
    buttons.append(
        dict(
             args=['visible', [False]*j + [True] + [False]*(f.shape[1]-1-j)],
                 label=f'R = {R_cuts[j].round(2)} m',
             method='restyle'
        )
    )
    
    
fig.update_layout(
    xaxis_title="f",
    updatemenus=list([
        dict(
            x=0,
            y=1.2,
            yanchor='top',
            buttons=buttons
        ),
    ]),
)

fig.show()